<a href="https://colab.research.google.com/github/Ryong1998/snowball/blob/main/4_Modeling.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

- https://pmorissette.github.io/bt/

# 백테스트팅

- 미래예측을 하는 모델을 생성하기에는 금리와 시장 상황에 따라 수익률이 천차만별
- 해당 기간동안의 해당 전략으로 ETF를 선별했을 때 어떤 수익률이 나왔는지 확인하는 과정 진행

## 데이터 불러오기

In [54]:
import pandas as pd
# 출력할 최대 컬럼 수를 설정 (예: 20개로 설정)
pd.set_option('display.max_columns', 30)
df_etf_evaluate = pd.read_pickle('/content/drive/MyDrive/snowball/data/After_data_preprocessing/df_etf_evaluate.pkl')
print(df_etf_evaluate.info())
df_etf_evaluate

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 228229 entries, 0 to 228228
Data columns (total 17 columns):
 #   Column                   Non-Null Count   Dtype         
---  ------                   --------------   -----         
 0   etf_code                 228229 non-null  int64         
 1   etf_date                 228229 non-null  datetime64[ns]
 2   etf_real_price           228229 non-null  float64       
 3   etf_price                228229 non-null  int64         
 4   etf_revenue              228229 non-null  float64       
 5   etf_operatingincomeloss  228229 non-null  float64       
 6   etf_profitloss           228229 non-null  float64       
 7   etf_assets               228229 non-null  float64       
 8   etf_liabilities          228229 non-null  float64       
 9   etf_equity               228229 non-null  float64       
 10  etf_per                  228229 non-null  float64       
 11  etf_pbr                  228229 non-null  float64       
 12  etf_psr         

etf_code   etf_date  etf_real_price  etf_price   etf_revenue  \
0          69500 2017-01-02     24383.71174      26415  38271.918037   
1          69500 2017-01-03     24593.71174      26625  38271.918037   
2          69500 2017-01-04     24623.71174      26655  38271.918037   
3          69500 2017-01-05     24518.71174      26550  38271.918037   
4          69500 2017-01-06     24633.71174      26665  38271.918037   
...          ...        ...             ...        ...           ...   
228224    448570 2022-12-23      9339.12918       9645  41237.154403   
228225    448570 2022-12-26      9324.12918       9630  41237.154403   
228226    448570 2022-12-27      9384.12918       9690  41237.154403   
228227    448570 2022-12-28      9384.12918       9690  41237.154403   
228228    448570 2022-12-29      9194.12918       9500  41237.154403   

        etf_operatingincomeloss  etf_profitloss    etf_assets  \
0                   3019.687683     2176.379620  89955.773639   
1                   3019.687683     2176.379620  89955.773639   
2                   3019.687683     2176.379620  89955.773639   
3                   3019.687683     2176.379620  89955.773639   
4                   3019.687683     2176.379620  89955.773639   
...                         ...             ...           ...   
228224              3062.602751     2214.324945  78988.223848   
228225              3062.602751     2214.324945  78988.223848   
228226              3062.602751     2214.324945  78988.223848   
228227              3062.602751     2214.324945  78988.223848   
228228              3062.602751     2214.324945  78988.223848   

        etf_liabilities    etf_equity    etf_per   etf_pbr   etf_psr  \
0          63346.245309  26609.528330  12.137129  0.992690  0.690193   
1          63346.245309  26609.528330  12.233619  1.000581  0.695680   
2          63346.245309  26609.528330  12.247404  1.001709  0.696464   
3          63346.245309  26609.528330  12.199159  0.997763  0.693720   
4          63346.245309  26609.528330  12.251999  1.002085  0.696725   
...                 ...           ...        ...       ...       ...   
228224     58725.799013  20262.424834   4.355729  0.476004  0.233891   
228225     58725.799013  20262.424834   4.348955  0.475264  0.233527   
228226     58725.799013  20262.424834   4.376052  0.478225  0.234982   
228227     58725.799013  20262.424834   4.376052  0.478225  0.234982   
228228     58725.799013  20262.424834   4.290247  0.468848  0.230375   

        etf_operating_ratio  etf_profit_ratio  etf_debt_ratio    etf_roe  
0                  7.890087          5.686623      238.058505   8.178949  
1                  7.890087          5.686623      238.058505   8.178949  
2                  7.890087          5.686623      238.058505   8.178949  
3                  7.890087          5.686623      238.058505   8.178949  
4                  7.890087          5.686623      238.058505   8.178949  
...                     ...               ...             ...        ...  
228224             7.426804          5.369733      289.826117  10.928233  
228225             7.426804          5.369733      289.826117  10.928233  
228226             7.426804          5.369733      289.826117  10.928233  
228227             7.426804          5.369733      289.826117  10.928233  
228228             7.426804          5.369733      289.826117  10.928233  

[228229 rows x 17 columns]

## 조회할 날짜 계산하는 함수 생성

In [55]:
etf_date_list = list(set(df_etf_evaluate['etf_date']))
etf_date_list = sorted(etf_date_list)
etf_date_list[:3]

[Timestamp('2017-01-02 00:00:00'),
 Timestamp('2017-01-03 00:00:00'),
 Timestamp('2017-01-04 00:00:00')]

In [56]:
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta

# 몇 개월 단위로 값들을 추가할
def get_specific_date(duration):
    date_list = []

    # 시작 날짜와 끝 날짜 설정
    start_date = datetime(2017, 1, 2)
    end_date = datetime(2022, 12, 29)

    date_list.append(start_date)

    current_date = start_date

    while current_date <= end_date:

      current_date += relativedelta(months=duration)
      next_date = current_date

      if current_date in etf_date_list:
          date_list.append(current_date)

      else:
        while (next_date not in date_list) and (next_date<datetime(2022, 12, 29)):
          next_date += timedelta(days=1)
          if next_date in etf_date_list:
              date_list.append(next_date)
              break

    date_list.append(end_date)

    return date_list



specific_date_list = get_specific_date(6)
specific_date_list


[datetime.datetime(2017, 1, 2, 0, 0),
 datetime.datetime(2017, 7, 3, 0, 0),
 datetime.datetime(2018, 1, 2, 0, 0),
 datetime.datetime(2018, 7, 2, 0, 0),
 datetime.datetime(2019, 1, 2, 0, 0),
 datetime.datetime(2019, 7, 2, 0, 0),
 datetime.datetime(2020, 1, 2, 0, 0),
 datetime.datetime(2020, 7, 2, 0, 0),
 datetime.datetime(2021, 1, 4, 0, 0),
 datetime.datetime(2021, 7, 2, 0, 0),
 datetime.datetime(2022, 1, 3, 0, 0),
 datetime.datetime(2022, 7, 4, 0, 0),
 datetime.datetime(2022, 12, 29, 0, 0)]

## KODEX 200 데이터프레임 생성

In [57]:
df_kodex_200 = df_etf_evaluate.loc[(df_etf_evaluate['etf_code']==69500),['etf_date','etf_price']].copy()
df_kodex_200.head()

etf_date  etf_price
0 2017-01-02      26415
1 2017-01-03      26625
2 2017-01-04      26655
3 2017-01-05      26550
4 2017-01-06      26665

In [58]:
df_kodex_200['return_rate'] = round((100*(df_kodex_200['etf_price'] - 26415))/26415, 2)
df_kodex_200

etf_date  etf_price  return_rate
0    2017-01-02      26415         0.00
1    2017-01-03      26625         0.80
2    2017-01-04      26655         0.91
3    2017-01-05      26550         0.51
4    2017-01-06      26665         0.95
...         ...        ...          ...
1470 2022-12-23      30235        14.46
1471 2022-12-26      30280        14.63
1472 2022-12-27      30495        15.45
1473 2022-12-28      30135        14.08
1474 2022-12-29      29595        12.04

[1475 rows x 3 columns]

## 수익률 그래프

In [59]:
df_etf_evaluate.loc[((df_etf_evaluate['etf_per']>=5)&(df_etf_evaluate['etf_per']<=8)&(df_etf_evaluate['etf_date']=='2017-01-02')),['etf_code','etf_price','etf_per']].sort_values('etf_per',ascending=False)

etf_code  etf_price   etf_per
5332       91180      17600  7.986440
34849     139250      12305  7.982803
100258    252650       9890  7.859806
28949     138540      18485  7.640226
68002     223190       7680  5.120652

In [60]:
etf_info = df_etf_evaluate.loc[((df_etf_evaluate['etf_per']>=5)&(df_etf_evaluate['etf_per']<=8)&(df_etf_evaluate['etf_date']=='2017-01-02')),['etf_code','etf_price','etf_per']].sort_values('etf_per').iloc[0]
etf_info

etf_code     223190.000000
etf_price      7680.000000
etf_per           5.120652
Name: 68002, dtype: float64

In [61]:
etf_info['etf_code']
etf_info['etf_price']

7680.0

#### 평가지표 따른 etf 정보 추출 함수

In [107]:
# 평가지표에 맞는 코드와 가격을 조회하는 함수 생성


def get_etf_code_price(strategy, min_num, max_num, date, asc): # asc True이면 값이 낮은것들이 나옴, False 이면 높은것들이 나옴
  if asc == True:
    try:
      etf_info = df_etf_evaluate.loc[((df_etf_evaluate[strategy]>min_num)&(df_etf_evaluate[strategy]<=max_num)&(df_etf_evaluate['etf_date']==date)),['etf_code','etf_price',strategy]].sort_values(strategy, ascending=True).iloc[0]
      return etf_info['etf_code'], etf_info['etf_price'], etf_info[strategy]
    except:
      return 'error'
  else:
    try:
      etf_info = df_etf_evaluate.loc[((df_etf_evaluate[strategy]>min_num)&(df_etf_evaluate[strategy]<=max_num)&(df_etf_evaluate['etf_date']==date)),['etf_code','etf_price',strategy]].sort_values(strategy, ascending=False).iloc[0]
      return etf_info['etf_code'], etf_info['etf_price'], etf_info[strategy]
    except:
      return 'error'




print(get_etf_code_price('etf_per', 5, 8, '2017-01-02', True))

(68002     223190
28949     138540
100258    252650
34849     139250
5332       91180
Name: etf_code, dtype: int64, 68002      7680
28949     18485
100258     9890
34849     12305
5332      17600
Name: etf_price, dtype: int64, 68002     5.120652
28949     7.640226
100258    7.859806
34849     7.982803
5332      7.986440
Name: etf_per, dtype: float64)


In [108]:
# 평가지표에 맞는 코드와 가격을 조회하는 함수 생성


def get_etf_code_price(strategy, min_num, max_num, date, asc): # asc True이면 값이 낮은것들이 나옴, False 이면 높은것들이 나옴
  if asc == True:
    try:
      etf_info = df_etf_evaluate.loc[((df_etf_evaluate[strategy]>min_num)&(df_etf_evaluate[strategy]<=max_num)&(df_etf_evaluate['etf_date']==date)),['etf_code','etf_price',strategy]].sort_values(strategy, ascending=True)
      return etf_info
    except:
      return 'error'
  else:
    try:
      etf_info = df_etf_evaluate.loc[((df_etf_evaluate[strategy]>min_num)&(df_etf_evaluate[strategy]<=max_num)&(df_etf_evaluate['etf_date']==date)),['etf_code','etf_price',strategy]].sort_values(strategy, ascending=False)
      return etf_info
    except:
      return 'error'




print(get_etf_code_price('etf_per', 5, 8, '2017-01-02', True))

        etf_code  etf_price   etf_per
68002     223190       7680  5.120652
28949     138540      18485  7.640226
100258    252650       9890  7.859806
34849     139250      12305  7.982803
5332       91180      17600  7.986440


### 수익률 계산 함수

In [63]:
import math
def get_return_rate(strategy, min_num, max_num, duration, asc):

  specific_date_list = get_specific_date(duration)

  etf_code = 0

  etf_price = 0
  etf_count = 0
  etf_value = 0

  start_money = 1000000

  return_rate =0
  return_rate_dict = dict()

  etf_code_dict = dict()
  strategy_score_dict = dict()

  for i,date in enumerate(etf_date_list): # 모든 날짜들에 대해서 진행
    if date in specific_date_list: # 상품조회 날짜인 경우
      if i ==0:
        if get_etf_code_price(strategy, min_num, max_num, date, asc) == 'error':
          return 'error', 'error','error'
        etf_code, etf_price, strategy_score = get_etf_code_price(strategy, min_num, max_num, date, asc) # 가장 첫번째 날짜는 금융상품과 가격 설정

        etf_count = start_money / etf_price
        etf_value = start_money

        return_rate_dict[date] =  0
        etf_code_dict[date] = etf_code
        strategy_score_dict[date] = strategy_score

      else:
        if get_etf_code_price(strategy, min_num, max_num, date, asc) == 'error':
          return 'error', 'error','error'

        etf_price = df_etf_evaluate.loc[(df_etf_evaluate['etf_code']==etf_code)&(df_etf_evaluate['etf_date']==date),'etf_price'].iloc[0] # 조회 가격 불러오기
        etf_value = etf_count * etf_price

        return_rate = (100*(etf_value - start_money)) /  start_money
        return_rate = round(return_rate,2)
        return_rate_dict[date] =  return_rate


        etf_code, etf_price, strategy_score = get_etf_code_price(strategy, min_num, max_num, date, asc) # 금융상품코드와 가격 갱신

        etf_count = etf_value / etf_price

        etf_code_dict[date] = etf_code
        strategy_score_dict[date] = strategy_score

    else:
      etf_price = df_etf_evaluate.loc[(df_etf_evaluate['etf_code']==etf_code)&(df_etf_evaluate['etf_date']==date),'etf_price'].iloc[0]

      etf_value = etf_count * etf_price

      return_rate = (100*(etf_value - start_money)) /  start_money
      return_rate = round(return_rate,2)
      return_rate_dict[date] =  return_rate


  return return_rate_dict, etf_code_dict, strategy_score_dict

return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate('etf_per', 0, 20, 3, True)
if return_rate_dict =='error':
  print('retry!! the range is error')
else:
  print(etf_code_dict)
  print(strategy_score_dict)

{Timestamp('2017-01-02 00:00:00'): 223190.0, Timestamp('2017-04-03 00:00:00'): 223190.0, Timestamp('2017-07-03 00:00:00'): 223190.0, Timestamp('2017-10-10 00:00:00'): 223190.0, Timestamp('2018-01-02 00:00:00'): 223190.0, Timestamp('2018-04-02 00:00:00'): 223190.0, Timestamp('2018-07-02 00:00:00'): 223190.0, Timestamp('2018-10-02 00:00:00'): 223190.0, Timestamp('2019-01-02 00:00:00'): 223190.0, Timestamp('2019-04-02 00:00:00'): 223190.0, Timestamp('2019-07-02 00:00:00'): 223190.0, Timestamp('2019-10-02 00:00:00'): 91170.0, Timestamp('2020-01-02 00:00:00'): 91220.0, Timestamp('2020-04-02 00:00:00'): 91220.0, Timestamp('2020-07-02 00:00:00'): 91220.0, Timestamp('2020-10-05 00:00:00'): 91220.0, Timestamp('2021-01-04 00:00:00'): 91220.0, Timestamp('2021-04-02 00:00:00'): 91220.0, Timestamp('2021-07-02 00:00:00'): 91220.0, Timestamp('2021-10-05 00:00:00'): 223190.0, Timestamp('2022-01-03 00:00:00'): 223190.0, Timestamp('2022-04-04 00:00:00'): 244670.0, Timestamp('2022-07-04 00:00:00'): 28502

In [64]:
etf_code_dict.keys()

dict_keys([Timestamp('2017-01-02 00:00:00'), Timestamp('2017-04-03 00:00:00'), Timestamp('2017-07-03 00:00:00'), Timestamp('2017-10-10 00:00:00'), Timestamp('2018-01-02 00:00:00'), Timestamp('2018-04-02 00:00:00'), Timestamp('2018-07-02 00:00:00'), Timestamp('2018-10-02 00:00:00'), Timestamp('2019-01-02 00:00:00'), Timestamp('2019-04-02 00:00:00'), Timestamp('2019-07-02 00:00:00'), Timestamp('2019-10-02 00:00:00'), Timestamp('2020-01-02 00:00:00'), Timestamp('2020-04-02 00:00:00'), Timestamp('2020-07-02 00:00:00'), Timestamp('2020-10-05 00:00:00'), Timestamp('2021-01-04 00:00:00'), Timestamp('2021-04-02 00:00:00'), Timestamp('2021-07-02 00:00:00'), Timestamp('2021-10-05 00:00:00'), Timestamp('2022-01-03 00:00:00'), Timestamp('2022-04-04 00:00:00'), Timestamp('2022-07-04 00:00:00'), Timestamp('2022-10-04 00:00:00'), Timestamp('2022-12-29 00:00:00')])

In [65]:
return_rate_dict

{Timestamp('2017-01-02 00:00:00'): 0,
 Timestamp('2017-01-03 00:00:00'): 1.11,
 Timestamp('2017-01-04 00:00:00'): 0.91,
 Timestamp('2017-01-05 00:00:00'): 0.39,
 Timestamp('2017-01-06 00:00:00'): 0.72,
 Timestamp('2017-01-09 00:00:00'): 1.37,
 Timestamp('2017-01-10 00:00:00'): 0.98,
 Timestamp('2017-01-11 00:00:00'): 2.08,
 Timestamp('2017-01-12 00:00:00'): 3.13,
 Timestamp('2017-01-13 00:00:00'): 2.6,
 Timestamp('2017-01-16 00:00:00'): 2.08,
 Timestamp('2017-01-17 00:00:00'): 2.47,
 Timestamp('2017-01-18 00:00:00'): 2.54,
 Timestamp('2017-01-19 00:00:00'): 2.67,
 Timestamp('2017-01-20 00:00:00'): 2.28,
 Timestamp('2017-01-23 00:00:00'): 2.28,
 Timestamp('2017-01-24 00:00:00'): 2.28,
 Timestamp('2017-01-25 00:00:00'): 2.54,
 Timestamp('2017-01-26 00:00:00'): 3.45,
 Timestamp('2017-01-31 00:00:00'): 2.28,
 Timestamp('2017-02-01 00:00:00'): 2.8,
 Timestamp('2017-02-02 00:00:00'): 2.34,
 Timestamp('2017-02-03 00:00:00'): 2.41,
 Timestamp('2017-02-06 00:00:00'): 2.47,
 Timestamp('2017-02-0

### 수익률 시각화 함수

In [66]:
import pandas as pd

df_result = pd.DataFrame(columns=['PER', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'volatility'])
df_result

Empty DataFrame
Columns: [PER, rebalance_cycle, final_return_rate, compare_kodex_200, volatility]
Index: []

In [67]:
df_kodex_200['daily_return_rate'] = df_kodex_200['return_rate'].shift(1)
df_kodex_200['daily_return_rate'] = df_kodex_200['return_rate'] -df_kodex_200['daily_return_rate']
df_kodex_200

etf_date  etf_price  return_rate  daily_return_rate
0    2017-01-02      26415         0.00                NaN
1    2017-01-03      26625         0.80               0.80
2    2017-01-04      26655         0.91               0.11
3    2017-01-05      26550         0.51              -0.40
4    2017-01-06      26665         0.95               0.44
...         ...        ...          ...                ...
1470 2022-12-23      30235        14.46              -2.01
1471 2022-12-26      30280        14.63               0.17
1472 2022-12-27      30495        15.45               0.82
1473 2022-12-28      30135        14.08              -1.37
1474 2022-12-29      29595        12.04              -2.04

[1475 rows x 4 columns]

In [68]:
import plotly.graph_objects as go
import numpy as np

def add_graph(fig,dictionary, strategy, min_num, max_num, duration):
  # 딕셔너리의 키와 값 추출
  keys = list(dictionary.keys())
  values = list(dictionary.values())

  # plotly의 line chart 생성
  # fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))



  # plotly의 line chart 생성
  fig.add_trace(go.Scatter(x=keys, y=values, mode='lines', name= strategy + ' '+str(min_num)+'~'+str(max_num)+' '+str(duration)+'m'))

  # 그래프 레이아웃 설정
  fig.update_layout(title=strategy +' 수익률 그래프',
                    xaxis_title='날짜',
                    yaxis_title='수익률 추이')


  strategy_range = str(min_num)+'~'+str(max_num)

  win_count =0

  for i,value in enumerate(values):
    if i ==0:
      continue

    daily_value = value - values[i-1]
    if value >= df_kodex_200.loc[i,'return_rate']:
      win_count+=1

  win_rate = round((100*win_count)/1474,2)

  strategy_volatility= np.std(values)



  return strategy_range, duration, dictionary[pd.Timestamp('2022-12-29 00:00:00')], win_rate, strategy_volatility


fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, 'etf_per', 0, 20, 3)
# 새로운 행을 추가할 데이터 리스트
new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]
# 데이터프레임에 새로운 행 추가
df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)


fig.show()

In [69]:
df_result

PER rebalance_cycle  final_return_rate  compare_kodex_200  volatility
0  0~20               3               1.39              23.47   12.504238

## PER

### 범위 정의

In [70]:
import numpy as np
df_per_not_inf = df_etf_evaluate.loc[df_etf_evaluate['etf_per']!=np.inf,:].copy()
df_per_not_inf

etf_code   etf_date  etf_real_price  etf_price   etf_revenue  \
0          69500 2017-01-02     24383.71174      26415  38271.918037   
1          69500 2017-01-03     24593.71174      26625  38271.918037   
2          69500 2017-01-04     24623.71174      26655  38271.918037   
3          69500 2017-01-05     24518.71174      26550  38271.918037   
4          69500 2017-01-06     24633.71174      26665  38271.918037   
...          ...        ...             ...        ...           ...   
228224    448570 2022-12-23      9339.12918       9645  41237.154403   
228225    448570 2022-12-26      9324.12918       9630  41237.154403   
228226    448570 2022-12-27      9384.12918       9690  41237.154403   
228227    448570 2022-12-28      9384.12918       9690  41237.154403   
228228    448570 2022-12-29      9194.12918       9500  41237.154403   

        etf_operatingincomeloss  etf_profitloss    etf_assets  \
0                   3019.687683     2176.379620  89955.773639   
1                   3019.687683     2176.379620  89955.773639   
2                   3019.687683     2176.379620  89955.773639   
3                   3019.687683     2176.379620  89955.773639   
4                   3019.687683     2176.379620  89955.773639   
...                         ...             ...           ...   
228224              3062.602751     2214.324945  78988.223848   
228225              3062.602751     2214.324945  78988.223848   
228226              3062.602751     2214.324945  78988.223848   
228227              3062.602751     2214.324945  78988.223848   
228228              3062.602751     2214.324945  78988.223848   

        etf_liabilities    etf_equity    etf_per   etf_pbr   etf_psr  \
0          63346.245309  26609.528330  12.137129  0.992690  0.690193   
1          63346.245309  26609.528330  12.233619  1.000581  0.695680   
2          63346.245309  26609.528330  12.247404  1.001709  0.696464   
3          63346.245309  26609.528330  12.199159  0.997763  0.693720   
4          63346.245309  26609.528330  12.251999  1.002085  0.696725   
...                 ...           ...        ...       ...       ...   
228224     58725.799013  20262.424834   4.355729  0.476004  0.233891   
228225     58725.799013  20262.424834   4.348955  0.475264  0.233527   
228226     58725.799013  20262.424834   4.376052  0.478225  0.234982   
228227     58725.799013  20262.424834   4.376052  0.478225  0.234982   
228228     58725.799013  20262.424834   4.290247  0.468848  0.230375   

        etf_operating_ratio  etf_profit_ratio  etf_debt_ratio    etf_roe  
0                  7.890087          5.686623      238.058505   8.178949  
1                  7.890087          5.686623      238.058505   8.178949  
2                  7.890087          5.686623      238.058505   8.178949  
3                  7.890087          5.686623      238.058505   8.178949  
4                  7.890087          5.686623      238.058505   8.178949  
...                     ...               ...             ...        ...  
228224             7.426804          5.369733      289.826117  10.928233  
228225             7.426804          5.369733      289.826117  10.928233  
228226             7.426804          5.369733      289.826117  10.928233  
228227             7.426804          5.369733      289.826117  10.928233  
228228             7.426804          5.369733      289.826117  10.928233  

[219282 rows x 17 columns]

In [71]:
result, bins = pd.qcut(df_per_not_inf['etf_per'], q=9, retbins=True)
# 결과를 리스트로 변환
results_list = result.cat.categories.tolist()

# 각 Interval을 리스트로 변환
range_list = [[round(interval.left,2), round(interval.right,2)] for interval in results_list]
range_list

[[2.66, 8.23],
 [8.23, 9.62],
 [9.62, 10.87],
 [10.87, 12.42],
 [12.42, 14.93],
 [14.93, 18.83],
 [18.83, 24.12],
 [24.12, 36.59],
 [36.59, 4186.06]]

In [72]:
for range in range_list:
  input_data = ('etf_per', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)
  if return_rate_dict =='error':
    print('retry!! the range is error')

### 낮은 수치 우선순위

In [73]:
import pandas as pd

df_result = pd.DataFrame(columns=['PER', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])
df_result

Empty DataFrame
Columns: [PER, rebalance_cycle, final_return_rate, compare_kodex_200, strategy_volatility]
Index: []

In [74]:
fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_per', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

PER rebalance_cycle  final_return_rate  compare_kodex_200  \
0      2.66~8.23               6               3.86              24.49   
1      8.23~9.62               6              16.58              11.47   
2     9.62~10.87               6              33.34              52.04   
3    10.87~12.42               6              22.54              48.37   
4    12.42~14.93               6              -7.20              18.79   
5    14.93~18.83               6              24.90              70.96   
6    18.83~24.12               6              54.31              55.43   
7    24.12~36.59               6              -2.94              17.91   
8  36.59~4186.06               6              -6.49               9.77   

   strategy_volatility  
0            12.302111  
1            15.219297  
2            36.821386  
3            20.990994  
4            16.992744  
5            39.661319  
6            31.661879  
7            16.040808  
8            25.709515

### 높은 수치 우선순위

In [75]:
import pandas as pd

df_result = pd.DataFrame(columns=['PER', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])
df_result

Empty DataFrame
Columns: [PER, rebalance_cycle, final_return_rate, compare_kodex_200, strategy_volatility]
Index: []

In [76]:
fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_per', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, False)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

PER rebalance_cycle  final_return_rate  compare_kodex_200  \
0      2.66~8.23               6               6.92               4.21   
1      8.23~9.62               6             -30.96               0.81   
2     9.62~10.87               6               3.94               0.54   
3    10.87~12.42               6             -18.95              18.18   
4    12.42~14.93               6             -15.12              53.05   
5    14.93~18.83               6             -22.69               6.31   
6    18.83~24.12               6              24.87              75.92   
7    24.12~36.59               6             -15.19              35.01   
8  36.59~4186.06               6              32.95              94.30   

   strategy_volatility  
0            15.893847  
1            13.383041  
2            15.630997  
3            14.745794  
4            19.955896  
5            13.321341  
6            20.519095  
7            21.021267  
8            38.905781

## PBR

### 범위 정의

In [77]:
result, bins = pd.qcut(df_per_not_inf['etf_pbr'], q=9, retbins=True)
# 결과를 리스트로 변환
results_list = result.cat.categories.tolist()

# 각 Interval을 리스트로 변환
range_list = [[round(interval.left,2), round(interval.right,2)] for interval in results_list]
range_list

[[0.21, 0.64],
 [0.64, 0.8],
 [0.8, 0.89],
 [0.89, 0.98],
 [0.98, 1.11],
 [1.11, 1.27],
 [1.27, 1.59],
 [1.59, 2.51],
 [2.51, 10.92]]

In [78]:
for range in range_list:
  input_data = ('etf_pbr', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)
  if return_rate_dict =='error':
    print('retry!! the range is error')

### 낮은 수치 우선순위

In [79]:
import pandas as pd

df_result = pd.DataFrame(columns=['PBR', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])
df_result

Empty DataFrame
Columns: [PBR, rebalance_cycle, final_return_rate, compare_kodex_200, strategy_volatility]
Index: []

In [80]:
fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_pbr', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

PBR rebalance_cycle  final_return_rate  compare_kodex_200  \
0   0.21~0.64               6              36.47              51.15   
1    0.64~0.8               6             -14.32               5.09   
2    0.8~0.89               6               1.26              14.52   
3   0.89~0.98               6              37.43              59.02   
4   0.98~1.11               6              33.34              90.57   
5   1.11~1.27               6               2.34               0.20   
6   1.27~1.59               6              35.40              74.49   
7   1.59~2.51               6              -9.19              54.14   
8  2.51~10.92               6             -38.63              43.42   

   strategy_volatility  
0            23.684768  
1            12.056844  
2            14.555381  
3            25.846947  
4            25.014841  
5            18.180522  
6            38.907988  
7            24.753231  
8            26.613571

### 높은 수치 우선순위

In [81]:
import pandas as pd

df_result = pd.DataFrame(columns=['PBR', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])

fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_pbr', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, False)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

PBR rebalance_cycle  final_return_rate  compare_kodex_200  \
0   0.21~0.64               6              -8.12              29.65   
1    0.64~0.8               6              21.71              43.76   
2    0.8~0.89               6              23.68              65.13   
3   0.89~0.98               6              15.29              23.07   
4   0.98~1.11               6               8.49              80.53   
5   1.11~1.27               6               4.59              34.40   
6   1.27~1.59               6              92.95              74.42   
7   1.59~2.51               6             -19.30              23.88   
8  2.51~10.92               6             -12.31              47.76   

   strategy_volatility  
0            11.988205  
1            16.503255  
2            23.550726  
3            27.397023  
4            21.617497  
5            19.412715  
6            49.301473  
7            15.284103  
8            31.421493

## PSR

### 범위 정의

In [82]:
result, bins = pd.qcut(df_per_not_inf['etf_psr'], q= 10, retbins=True)
# 결과를 리스트로 변환
results_list = result.cat.categories.tolist()

# 각 Interval을 리스트로 변환
range_list = [[round(interval.left,2), round(interval.right,2)] for interval in results_list]
range_list

[[0.11, 0.36],
 [0.36, 0.46],
 [0.46, 0.56],
 [0.56, 0.65],
 [0.65, 0.72],
 [0.72, 0.82],
 [0.82, 0.99],
 [0.99, 1.35],
 [1.35, 2.44],
 [2.44, 17.92]]

In [83]:
for range in range_list:
  input_data = ('etf_psr', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)
  if return_rate_dict =='error':
    print('retry!! the range is error')

### 낮은 수치 우선순위

In [84]:
import pandas as pd

df_result = pd.DataFrame(columns=['PSR', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])
df_result

Empty DataFrame
Columns: [PSR, rebalance_cycle, final_return_rate, compare_kodex_200, strategy_volatility]
Index: []

In [85]:
fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_psr', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

PSR rebalance_cycle  final_return_rate  compare_kodex_200  \
0   0.11~0.36               6               7.11               0.20   
1   0.36~0.46               6              26.66              19.00   
2   0.46~0.56               6             -12.89               1.36   
3   0.56~0.65               6              17.30              35.48   
4   0.65~0.72               6              58.19              49.32   
5   0.72~0.82               6              15.61              10.65   
6   0.82~0.99               6               5.61               3.05   
7   0.99~1.35               6              -2.24              62.48   
8   1.35~2.44               6              30.05              49.93   
9  2.44~17.92               6              42.41              87.31   

   strategy_volatility  
0            16.438206  
1            22.831178  
2            13.383048  
3            20.950609  
4            47.850389  
5            19.831394  
6            19.090669  
7            12.023997  
8            32.340021  
9            42.868229


### 높은 수치 우선순위

In [86]:
import pandas as pd

df_result = pd.DataFrame(columns=['PSR', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])

fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_psr', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, False)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

PSR rebalance_cycle  final_return_rate  compare_kodex_200  \
0   0.11~0.36               6              16.75               3.46   
1   0.36~0.46               6             -16.41               0.68   
2   0.46~0.56               6              19.67              29.92   
3   0.56~0.65               6              23.70              37.92   
4   0.65~0.72               6              35.74              88.33   
5   0.72~0.82               6              10.72              27.14   
6   0.82~0.99               6              12.88              71.57   
7   0.99~1.35               6             -25.05              19.54   
8   1.35~2.44               6              50.73              99.73   
9  2.44~17.92               6             -12.31              47.76   

   strategy_volatility  
0            15.909378  
1            12.011313  
2            22.443611  
3            23.455400  
4            25.088680  
5            18.287385  
6            16.116870  
7            19.664697  
8            46.015091  
9            31.421493

## 영업이익률

### 범위 정의

In [87]:
result, bins = pd.qcut(df_etf_evaluate['etf_operating_ratio'], q=10, retbins=True)
# 결과를 리스트로 변환
results_list = result.cat.categories.tolist()

# 각 Interval을 리스트로 변환
range_list = [[round(interval.left,2), round(interval.right,2)] for interval in results_list]
range_list

[[-15.16, 4.2],
 [4.2, 5.4],
 [5.4, 6.01],
 [6.01, 6.67],
 [6.67, 7.36],
 [7.36, 8.16],
 [8.16, 8.95],
 [8.95, 9.82],
 [9.82, 11.13],
 [11.13, 30.84]]

In [88]:
for range in range_list:
  input_data = ('etf_operating_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)
  if return_rate_dict =='error':
    print('retry!! the range is error')

### 낮은 수치 우선순위

In [89]:
import pandas as pd

df_result = pd.DataFrame(columns=['Operating_Ratio', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])
df_result

Empty DataFrame
Columns: [Operating_Ratio, rebalance_cycle, final_return_rate, compare_kodex_200, strategy_volatility]
Index: []

In [90]:
fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_operating_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

Operating_Ratio rebalance_cycle  final_return_rate  compare_kodex_200  \
0      -15.16~4.2               6             -38.85               5.36   
1         4.2~5.4               6             -23.11               9.36   
2        5.4~6.01               6              13.68              28.22   
3       6.01~6.67               6              18.56              21.30   
4       6.67~7.36               6              28.68              29.44   
5       7.36~8.16               6             -24.73              31.14   
6       8.16~8.95               6              84.15             100.00   
7       8.95~9.82               6              25.48              31.21   
8      9.82~11.13               6              11.76              24.56   
9     11.13~30.84               6              -1.61              81.21   

   strategy_volatility  
0            18.626583  
1            15.638691  
2            14.792208  
3            26.399957  
4            23.398039  
5            17.887911  
6            39.621184  
7            20.011213  
8            24.401211  
9            37.071990

### 높은 수치 우선 순위

In [91]:
import pandas as pd

df_result = pd.DataFrame(columns=['Operating_Ratio', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])

fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_operating_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, False)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

Operating_Ratio rebalance_cycle  final_return_rate  compare_kodex_200  \
0      -15.16~4.2               6             -19.59               5.09   
1         4.2~5.4               6              53.34              43.49   
2        5.4~6.01               6              -4.20               9.77   
3       6.01~6.67               6              20.68              41.86   
4       6.67~7.36               6              64.08              88.40   
5       7.36~8.16               6              49.84              88.40   
6       8.16~8.95               6              64.59              95.32   
7       8.95~9.82               6               4.31              17.16   
8      9.82~11.13               6             -20.73               2.51   
9     11.13~30.84               6              -2.93              31.95   

   strategy_volatility  
0            12.655093  
1            24.460406  
2            17.457917  
3            29.853720  
4            38.045961  
5            28.241607  
6            35.049392  
7            15.194977  
8            11.907577  
9            25.887636

### duration 변경

## 순이익률

### 범위 정의

In [92]:
result, bins = pd.qcut(df_etf_evaluate['etf_profit_ratio'], q=8, retbins=True)
# 결과를 리스트로 변환
results_list = result.cat.categories.tolist()

# 각 Interval을 리스트로 변환
range_list = [[round(interval.left,2), round(interval.right,2)] for interval in results_list]
range_list

[[-26.0, 2.28],
 [2.28, 3.57],
 [3.57, 4.54],
 [4.54, 5.49],
 [5.49, 6.51],
 [6.51, 7.65],
 [7.65, 8.93],
 [8.93, 55.83]]

In [93]:
for range in range_list:
  input_data = ('etf_profit_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)
  if return_rate_dict =='error':
    print('retry!! the range is error')

### 낮은 수치 우선순위

In [94]:
import pandas as pd

df_result = pd.DataFrame(columns=['Profit_Ratio', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])
df_result

Empty DataFrame
Columns: [Profit_Ratio, rebalance_cycle, final_return_rate, compare_kodex_200, strategy_volatility]
Index: []

In [95]:
fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_profit_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

Profit_Ratio rebalance_cycle  final_return_rate  compare_kodex_200  \
0   -26.0~2.28               6              -0.87              15.33   
1    2.28~3.57               6              48.71              90.71   
2    3.57~4.54               6               0.48               1.36   
3    4.54~5.49               6              19.34              59.57   
4    5.49~6.51               6             -11.52               0.68   
5    6.51~7.65               6               0.93               1.70   
6    7.65~8.93               6              51.61              88.94   
7   8.93~55.83               6              68.05              90.71   

   strategy_volatility  
0            20.376356  
1            21.535844  
2            17.807115  
3            23.920735  
4            14.983384  
5            10.494497  
6            41.162559  
7            34.659220

### 높은 수치 우선순위

In [96]:
import pandas as pd

df_result = pd.DataFrame(columns=['Operating_Ratio', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])

fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_profit_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, False)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

Operating_Ratio rebalance_cycle  final_return_rate  compare_kodex_200  \
0      -26.0~2.28               6             -25.62               0.54   
1       2.28~3.57               6              65.87              87.38   
2       3.57~4.54               6              10.09              42.54   
3       4.54~5.49               6             -10.63               0.27   
4       5.49~6.51               6              22.35              60.24   
5       6.51~7.65               6              23.47              78.77   
6       7.65~8.93               6              49.96              89.15   
7      8.93~55.83               6             -37.47              34.33   

   strategy_volatility  
0            13.257658  
1            32.596795  
2            14.995240  
3            12.918974  
4            22.636821  
5            20.155703  
6            39.307356  
7            32.977717

## 부채비율

### 범위 정의

In [97]:
result, bins = pd.qcut(df_etf_evaluate['etf_debt_ratio'], q=7, retbins=True)
# 결과를 리스트로 변환
results_list = result.cat.categories.tolist()

# 각 Interval을 리스트로 변환
range_list = [[round(interval.left,2), round(interval.right,2)] for interval in results_list]
range_list

[[24.87, 73.76],
 [73.76, 103.54],
 [103.54, 129.78],
 [129.78, 216.18],
 [216.18, 259.21],
 [259.21, 289.06],
 [289.06, 1395.38]]

In [98]:
for range in range_list:
  input_data = ('etf_debt_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)
  if return_rate_dict =='error':
    print('retry!! the range is error')

### 낮은 수치 우선순위

In [99]:
import pandas as pd

df_result = pd.DataFrame(columns=['Debt_Ratio', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])
df_result

Empty DataFrame
Columns: [Debt_Ratio, rebalance_cycle, final_return_rate, compare_kodex_200, strategy_volatility]
Index: []

In [100]:
fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_debt_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

Debt_Ratio rebalance_cycle  final_return_rate  compare_kodex_200  \
0     24.87~73.76               6              47.64              48.85   
1    73.76~103.54               6              91.42              92.06   
2   103.54~129.78               6             -27.38               3.66   
3   129.78~216.18               6             -28.17              12.62   
4   216.18~259.21               6              15.66              98.03   
5   259.21~289.06               6               9.14               1.02   
6  289.06~1395.38               6              47.87              99.46   

   strategy_volatility  
0            33.362602  
1            49.464719  
2            16.341166  
3            13.473974  
4            22.662158  
5            21.192767  
6            24.363979

### 높은 수치 우선 순위

In [101]:
df_result = pd.DataFrame(columns=['Debt_Ratio', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])

for range in range_list:
  input_data = ('etf_debt_ratio', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, False)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

Debt_Ratio rebalance_cycle  final_return_rate  compare_kodex_200  \
0     24.87~73.76               6              67.55              93.96   
1    73.76~103.54               6              56.90              46.88   
2   103.54~129.78               6              36.66              92.88   
3   129.78~216.18               6              50.88              81.07   
4   216.18~259.21               6              10.37              47.90   
5   259.21~289.06               6              21.45              38.06   
6  289.06~1395.38               6              -7.70              41.45   

   strategy_volatility  
0            32.854160  
1            53.604090  
2            23.437993  
3            26.352017  
4            13.810460  
5            22.956041  
6            17.755244

## ROE

### 범위 정의

In [102]:
result, bins = pd.qcut(df_etf_evaluate['etf_roe'], q=5, retbins=True)
# 결과를 리스트로 변환
results_list = result.cat.categories.tolist()

# 각 Interval을 리스트로 변환
range_list = [[round(interval.left,2), round(interval.right,2)] for interval in results_list]
range_list

[[-35.99, 4.51], [4.51, 7.05], [7.05, 8.93], [8.93, 10.55], [10.55, 35.26]]

In [103]:
for range in range_list:
  input_data = ('etf_roe', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)
  if return_rate_dict =='error':
    print('retry!! the range is error')

### 낮은 수치 우선순위

In [104]:
import pandas as pd

df_result = pd.DataFrame(columns=['ROE', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])
df_result

Empty DataFrame
Columns: [ROE, rebalance_cycle, final_return_rate, compare_kodex_200, strategy_volatility]
Index: []

In [105]:
fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_roe', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, True)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

ROE rebalance_cycle  final_return_rate  compare_kodex_200  \
0  -35.99~4.51               6               5.22              28.43   
1    4.51~7.05               6             -34.67               1.36   
2    7.05~8.93               6              58.94              58.21   
3   8.93~10.55               6             -12.82               1.70   
4  10.55~35.26               6             -20.99               8.89   

   strategy_volatility  
0            21.700922  
1            13.818568  
2            42.444106  
3             7.250638  
4            14.327111

### 높은 수치 우선순위

In [106]:
df_result = pd.DataFrame(columns=['ROE', 'rebalance_cycle','final_return_rate', 'compare_kodex_200', 'strategy_volatility'])

fig = go.Figure(data=go.Scatter(x=df_kodex_200['etf_date'], y=df_kodex_200['return_rate'], mode='lines', name='Kodex 200'))

for range in range_list:
  input_data = ('etf_roe', range[0], range[1], 6)
  return_rate_dict, etf_code_dict, strategy_score_dict = get_return_rate(*input_data, False)

  strategy_range, duration, final_return_rate, win_rate, strategy_volatility = add_graph(fig,return_rate_dict, *input_data)

  new_row_data = [strategy_range, duration, final_return_rate, win_rate, strategy_volatility]

  df_result = pd.concat([df_result, pd.DataFrame([new_row_data], columns=df_result.columns)], ignore_index=True)

fig.show()
display(df_result)

ROE rebalance_cycle  final_return_rate  compare_kodex_200  \
0  -35.99~4.51               6              26.38              72.80   
1    4.51~7.05               6              28.12              91.25   
2    7.05~8.93               6               3.12               2.37   
3   8.93~10.55               6               1.48              43.76   
4  10.55~35.26               6             -50.40              10.65   

   strategy_volatility  
0            32.594494  
1            30.734740  
2            11.308539  
3            15.603458  
4            21.473090